In [1]:
# coding: utf-8
import warnings
warnings.filterwarnings('ignore')
import time
import os
import numpy as np
import keras
from keras import metrics
from keras.utils import to_categorical
from keras.models import load_model
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
from keras.models import Sequential
from keras.layers import Dense, Dropout, Flatten, Conv2D, MaxPooling2D,Activation
from keras.layers.embeddings import Embedding
from datetime import datetime
from gensim.models import word2vec
from collections import *
import pandas as pd

Using TensorFlow backend.


In [2]:
# get data
# get texts data
category2idx = {'AllTogether': 0, 'Baseball': 1, 'Boy-Girl': 2, 'C_chat':  3, 'CVS': 4,
                  'GameSale': 5, 'GetMarry': 6, 'Lifeismoney': 7, 'LoL': 8, 'MH': 9, 'MLB': 10, 'Mobilecomm': 11, 
                'movie': 12,'MuscleBeach':  13, 'NBA': 14,  'SENIORHIGH': 15, 'Stock': 16, 
                'Tennis': 17, 'Tos': 18, 'WomenTalk': 19}

train_df_sample = pd.read_pickle('train.pkl').sample(frac=1, random_state=123)

In [3]:
# print(type(train_df_sample), len(train_df_sample))
# print(train_df_sample.label)

In [4]:
train_texts = train_df_sample.values
label_list = train_df_sample.label

test_pickle_df = pd.read_pickle('test.pkl')
test_texts = test_pickle_df["text"].values
# print(len(test_texts), test_texts[0]) 

In [5]:
train_texts_list = []
for text in train_texts:
    train_texts_list.append(text[0])
# print(len(train_texts_list), train_texts_list[0])

In [6]:
# get word embedding vector
answer = word2vec.Word2Vec.load("word2vec_20180430.model")
word_vectors = answer.wv
wvv = word_vectors.vocab
wvv_keys = wvv.keys()
wvv_keys_list = list(wvv_keys)

In [7]:
# print(train_texts_list[0])

In [8]:
texts_list = []
for text in train_texts_list:
#     print(text)
    texts_list.append(text)
    
for text in test_texts:
    texts_list.append(text)

['上次', '板友文', '日期', '928', '神魔', 'ID216883296', '常掛', '代表', '黑狗', '更換', '代表', '暫時', '黑狗', '徵求', '好友', '大聖過', '小丑', '自介', '每週', '一次', '小丑', '日誠徵大聖', '支援']
['季前', '有人', '提到', '球季', '挑戰', '72', '勝的', '球隊', '心目', '中', '是不是', '湖人', '熱火', '兩個', '選項', '有人', '說', '球季', '30', '場馬', '刺隊', '站上', '全聯盟', '第一', '勝率', '逼近', '九成', '你會', '覺得', '瘋', '25', '勝', '敗', '這是', '馬', '刺隊', '完前', '三分之一', '賽程', '戰績', '季初', '十二', '連勝', '後', '近期', '又拉出', '一波', '十連勝', '本篇', '文章', '將和', '一起', '探討', '開季', '至今', '馬', '刺', '大小事', '接下', '來進', '入球', '季', '中段', '展望', '隱憂', '所在', '球', '隊續', '約', '四年', '五千', '萬', '漲幅', '第四年', '部份', '保障', '350', '萬', '受傷', '右側', '第五', '蹠', '骨', '應力', '性骨折', '預計', '缺賽', '八週', '月初', '被裁', '補上', '第三', '控衛', '位置', '被裁', '回鍋', 'EvaLongoria', '辦理', '離婚', '右腳', '大拇指', '扭傷', '歸期', '未定', '勝的', '一開始', '談談', '最勁', '爆', '話題', '時', '尚早', '陸陸續續', '已經', '有人', '嗅到', '一些', '期待', '味道', '照理', '說', '應該', '完', '球季', '賽', '一半左右', '準不過', '這是', '建立', '這支', '球隊', '破紀錄', '期待', '心理', '情況', '下', '問筆者', '意見', '我會', '說', 

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




['問題', '一部分', '擴散', '箭', '我現', '喜歡', '弓箭', '擴散', '貫通', '擴散', '輸出', '主力', '使用', '貫通', '去貫', '最', '後', '一段', '使用', '增彈', '話', '擴散', '灑毒', '只能', '灑毒', '朋友', '說', '擴散', '於灑', '特殊', '狀態', '瓶蓄', '積值', '比例', '比較', '高且', '這把', '有毒', '強化', '知道', '灑毒', '以外', '擴散', '箭', '發揮', '地方', '論輸出', '清理', '小怪連', '射箭', '還比較', '優秀', '大型', '魔物', '貫通', '比較', '高傷', '擴散箭還', '有用', '弓箭', '迴', '避', '我現', '穿著', '長', '髮', '迅龍槍', '手裝', '弓箭', '使用', '迴', '避', '迴', '避距離', '增加', '先不論', '高級', '耳栓', '高級', '吼叫', '弓箭', '後', '跳', '退步', '辦法', '閃掉', '說', '滾', '每次', '夫魯要', '吼', '太早', '滾', '滾', '被定', '住', '說', '根本', '閃不掉', '成功', '退步', '閃毒', '鳥', '閃光', '感覺', '迴', '避', '迴', '避距離', '增加', '弓箭', '好', '發揮', '玩大劍', '感覺', '更爽', '注意', '方面', '嗎關', '技巧', '方面', '感謝', '回答']
['文章', '代碼', '作者', '阿鈞', '看板', '標題', '買賣', '明天', '412', '象猿', '張', '時間', '上禮', '拜', '買', '好票', '最近', '鋒哥', '高掛', '免戰牌', '只', '認識', '這兩個', '人', '朋友', '不想', '只好', '賣出', '兩', '張學', '生票', '西下', '區', '排', '號', '10', '號應', '不錯', '位置', '三壘', '辣', '米糕', '側兩', '張學', '生票', '350', '明天

KeyboardInterrupt: 

In [ ]:
print(type(texts_list), len(texts_list))

In [ ]:
del word_vectors, wvv, train_texts_list
# print(texts_list[0], "\n")
# print(texts_list[1], "\n")
# print(texts_list[2], "\n")

In [ ]:
tokenizer1 = Tokenizer(num_words = None)
tokenizer1.fit_on_texts(texts_list)
sequences = tokenizer1.texts_to_sequences(texts_list)  # word index list
max_doc_word_length = 200
sequences1 = pad_sequences(sequences, maxlen=max_doc_word_length, padding='post')
word_index = tokenizer1.word_index
print("Found %s unique tokens" % len(tokenizer1.word_index))
print( len(sequences1), tokenizer1.num_words) 

In [ ]:
vocab_size = len(word_index) + 1
# create a weight matrix for words in training docs
embedding_matrix = np.zeros((vocab_size, 250))
for word, i in word_index.items():
    if word in wvv_keys_list:
        embedding_vector = answer[word]
#         if embedding_vector is not None:
        embedding_matrix[i] = embedding_vector
    else:
        embedding_matrix[i] = np.zeros((1, 250))

In [ ]:
del answer

In [ ]:
# network model

def getModel(embedding_layer, image_width, image_height, input_channel):
    model = Sequential()
    model.add(embedding_layer)
    conv2D = Conv2D(filters=9, kernel_size = (3,3),
                padding = 'same', 
                input_shape = (image_width, image_height, input_channel))
    model.add(conv2D)
    model.add(MaxPooling2D(pool_size=(2,2)))    
    model.add(Flatten() )
    model.add(Dense(10, activation='softplus'))
    return model

In [ ]:
image_width = 250
image_height = 3
input_channel = 1

embedding_layer = Embedding(input_dim= embedding_matrix.shape[0],
                            output_dim= embedding_matrix.shape[1],
                            weights=[embedding_matrix], 
                            trainable=False)
model = getModel(embedding_layer, image_width, image_height, input_channel)
# early_stopping = keras.callbacks.EarlyStopping(monitor='val_loss', min_delta=0.00001, patience=0, verbose=0, mode='auto')
model.compile(optimizer='adam',loss='categorical_crossentropy',  metrics=["accuracy"])
model.summary()

In [ ]:
history = model.fit(x = sequences1[0:36000], y = label_list, 
                    validation_split=0.1, 
                    batch_size= 18000,
                    epochs = 100, verbose = 1)

In [ ]:
# model.save('my_model.h5') 

In [ ]:
# evaluate the model
loss_accuracy = model.evaluate(sequences1[0:100], label_list[0:100], verbose=1)
print(type(loss_accuracy), loss_accuracy)

In [ ]:
test_sequences1 = sequences1[9000:10000]

print(len(sequences1))
print(len(test_sequences1))

In [ ]:
predict_res = model.predict(test_sequences1, batch_size= 32, verbose=0)
print(len(predict_res), predict_res)

final_res = []
for pre_res in predict_res:
    final_res.append(np.argmax(pre_res))
print(final_res)

In [ ]:
# result_txt = "result" + str(datetime.now()).split()[1] + ".txt"
print(len(final_res))
result_txt = "server_result001" + ".txt"
ids = 0
with open(result_txt, 'w') as out:
    out.write("id,category" + '\n')
    for value in final_res:
        out.write(str(ids) + "," + str(value) + '\n')
        ids += 1